In [2]:
from re import sub
from gensim.utils import simple_preprocess
import gensim.downloader as api
from gensim.corpora import Dictionary
from gensim.models import TfidfModel
from gensim.models import WordEmbeddingSimilarityIndex
from gensim.similarities import SparseTermSimilarityMatrix
from gensim.similarities import SoftCosineSimilarity
import numpy as np
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import linear_kernel
from nltk import word_tokenize          
from nltk.stem import WordNetLemmatizer
import nltk
from nltk.corpus import stopwords
import pandas as pd

C:\Users\gopin\Anaconda3\lib\site-packages\numpy\_distributor_init.py:32: UserWarning: loaded more than 1 DLL from .libs:
C:\Users\gopin\Anaconda3\lib\site-packages\numpy\.libs\libopenblas.NOIJJG62EMASZI6NYURL6JBKM4EVBGM7.gfortran-win_amd64.dll
C:\Users\gopin\Anaconda3\lib\site-packages\numpy\.libs\libopenblas.TXA6YQSD3GCQQC22GEQ54J2UDCXDXHWN.gfortran-win_amd64.dll
  stacklevel=1)


In [3]:
# Load the model: this is a big file, can take a while to download and open
glove = api.load("glove-wiki-gigaword-50")    
similarity_index = WordEmbeddingSimilarityIndex(glove)

In [4]:
# Download stopwords list
stopwords = nltk.corpus.stopwords.words('english')
stopwords.append('Known')
stopwords.append('Recommended')
stopwords.append('places')
stopwords.append('visit')
stopwords.append('recommended')
stopwords.append('known')

In [5]:
# From: https://github.com/RaRe-Technologies/gensim/blob/develop/docs/notebooks/soft_cosine_tutorial.ipynb
def preprocess(doc):
    # Tokenize, clean up input document string
    doc = sub(r'<img[^<>]+(>|$)', " image_token ", doc)
    doc = sub(r'<[^<>]+(>|$)', " ", doc)
    doc = sub(r'\[img_assist[^]]*?\]', " ", doc)
    doc = sub(r'http[s]?://(?:[a-zA-Z]|[0-9]|[$-_@.&+]|[!*\(\),]|(?:%[0-9a-fA-F][0-9a-fA-F]))+', " url_token ", doc)
    return [token for token in simple_preprocess(doc, min_len=0, max_len=float("inf")) if token not in stopwords]

In [57]:
# Preprocess the documents, including the query string
corpus = [preprocess(document) for document in documents]
query = preprocess(query_string)

# Build the term dictionary, TF-idf model
dictionary = Dictionary(corpus+[query])
tfidf = TfidfModel(dictionary=dictionary)

# Create the term similarity matrix.  
similarity_matrix = SparseTermSimilarityMatrix(similarity_index, dictionary, tfidf)

query_tf = tfidf[dictionary.doc2bow(query)]

index = SoftCosineSimilarity(
            tfidf[[dictionary.doc2bow(document) for document in corpus]],
            similarity_matrix)

doc_similarity_scores = index[query_tf]

# Output the sorted similarity scores and documents
sorted_indexes = np.argsort(doc_similarity_scores)[::-1]
for idx in sorted_indexes:
    print(f'{idx} \t {doc_similarity_scores[idx]:0.3f} \t {documents[idx]}')

1 	 0.220 	 Prosperous, clean and orderly island city-state, with a Chinese majority but with strong Malay and Indian communities, the main business and financial hub of the region.
0 	 0.145 	 Known for coffee. Recommended places to visit are Dubai Museum, Burj Khalifa and Wild Wadi Water Park.


In [6]:
# reading the CSV file into pandas dataframe
Location_Data_df = pd.read_csv("Location_Data.csv")

In [9]:
Location_Data_df

Location_ID                Parent_ID             Name  \
0                          London           United_Kingdom           London   
1                           Dubai     United_Arab_Emirates            Dubai   
2                       Singapore                      NaN        Singapore   
3                       Amsterdam  wv__Western_Netherlands        Amsterdam   
4                           Paris     wv__C38Ele-de-France            Paris   
..                            ...                      ...              ...   
402                       Hanover         wv__Lower_Saxony          Hanover   
403        Kansas_City2C_Missouri                 Missouri      Kansas City   
404           Madison2C_Wisconsin                Wisconsin          Madison   
405  Manhattan_Beach2C_California               California  Manhattan Beach   
406                      Virginia            United_States         Virginia   

               Country_ID        Type  \
0          United_Kingdom        city   
1    United_Arab_Emirates        city   
2               Singapore  city_state   
3             Netherlands        city   
4                  France        city   
..                    ...         ...   
402               Germany        city   
403         United_States        city   
404         United_States        city   
405         United_States        city   
406         United_States      region   

                                               Snippet  Snippet_Language  \
0    Europe's financial metropolis and the former h...               NaN   
1    Known for coffee. Recommended places to visit ...               NaN   
2    Prosperous, clean and orderly island city-stat...               NaN   
3    Canals, Rembrandt, hashish and red lanterns, t...               NaN   
4    The "City of Light" and one of the most visite...               NaN   
..                                                 ...               ...   
402  Known for relax in a park. Recommended places ...               NaN   
403  Known for dinner. Recommended places to visit ...               NaN   
404  Known for places to eat and drink. Recommended...               NaN   
405  Known for beaches. Recommended places to visit...               NaN   
406  The DC suburbs of Northern Virginia contrast w...               NaN   

     Temp_Avg_Min_Jan  Temp_Avg_Max_Jan  Temp_Avg_Min_Feb  ...  \
0            2.300000          8.100000          2.100000  ...   
1           14.300000         23.900000         15.500000  ...   
2           23.900000         30.400000         24.300000  ...   
3            0.800000          5.800000          0.500000  ...   
4            2.000000          6.850000          2.150000  ...   
..                ...               ...               ...  ...   
402         -1.100000          4.000000         -1.100000  ...   
403         -6.111111          3.750000         -3.861111  ...   
404        -11.611111         -3.111111         -9.388889  ...   
405          9.611111         18.277778         10.111111  ...   
406               NaN               NaN               NaN  ...   

     Temp_Avg_Min_Aug  Temp_Avg_Max_Aug  Temp_Avg_Min_Sep  Temp_Avg_Max_Sep  \
0           13.700000         23.200000         11.400000         20.000000   
1           30.400000         41.300000         27.700000         38.900000   
2           25.000000         31.400000         24.800000         31.400000   
3           12.800000         22.100000         10.600000         18.800000   
4           14.200000         24.200000         11.850000         21.000000   
..                ...               ...               ...               ...   
402         12.900000         23.200000          9.900000         18.900000   
403         20.277778         31.111111         14.944444         26.388889   
404         15.000000         26.333333         10.111111         22.111111   
405         18.000000         24.000000         17.166667         23.833333   
406  

In [36]:
Similarity_Dict = {}

In [37]:
for i in range(407):

    city = Location_Data_df.iloc[i,0]
    city_desc = Location_Data_df.iloc[i,5]

    Compare_City = Location_Data_df[Location_Data_df["Location_ID"] !=Location_Data_df.iloc[i,0]]
    Compare_City = Compare_City.reset_index()
    Compare_City = Compare_City.drop(columns='index')

    Compare_City_Desc = Compare_City['Snippet'].tolist()

    # Preprocess the documents, including the query string
    corpus = [preprocess(document) for document in Compare_City_Desc]
    query = preprocess(city_desc)

    # Build the term dictionary, TF-idf model
    dictionary = Dictionary(corpus+[query])
    tfidf = TfidfModel(dictionary=dictionary)

    # Create the term similarity matrix.  
    similarity_matrix = SparseTermSimilarityMatrix(similarity_index, dictionary, tfidf)

    query_tf = tfidf[dictionary.doc2bow(query)]

    index = SoftCosineSimilarity(
                tfidf[[dictionary.doc2bow(document) for document in corpus]],
                similarity_matrix)

    doc_similarity_scores = index[query_tf]

    # Output the sorted similarity scores and documents
    sorted_indexes = np.argsort(doc_similarity_scores)[::-1]
    temp_df = Compare_City.iloc[sorted_indexes,:]
    temp_df['Similarity_Score'] = doc_similarity_scores[sorted_indexes]
    Similarity_Dict[city] = temp_df
    print(i)

C:\Users\gopin\Anaconda3\lib\site-packages\gensim\similarities\termsim.py:358: RuntimeWarning: divide by zero encountered in true_divide
  Y = np.multiply(Y, 1 / np.sqrt(Y_norm))
C:\Users\gopin\Anaconda3\lib\site-packages\gensim\similarities\termsim.py:358: RuntimeWarning: invalid value encountered in multiply
  Y = np.multiply(Y, 1 / np.sqrt(Y_norm))
C:\Users\gopin\Anaconda3\lib\site-packages\ipykernel_launcher.py:34: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

In [38]:
import csv
import pandas as pd 

def saver(dictex):
    for key, val in dictex.items():
        val.to_csv("Data/data_{}.csv".format(str(key)))

    with open("Data/keys.txt", "w") as f: #saving keys to file
        f.write(str(list(dictex.keys())))

def loader():
    """Reading data from keys"""
    with open("Data/keys.txt", "r") as f:
        keys = eval(f.read())

    dictex = {}    
    for key in keys:
        dictex[key] = pd.read_csv("Data/data_{}.csv".format(str(key)))

    return dictex

In [39]:
saver(Similarity_Dict)

In [33]:
dictex = loader()

In [34]:
dictex

{'London':      Unnamed: 0    Location_ID                     Parent_ID           Name  \
 0           130  New_York_City            New_York_28state29  New York City   
 1            18       Budapest           wv__Central_Hungary       Budapest   
 2           154  wv__Hong_Kong                         China      Hong Kong   
 3           236      Cleveland                          Ohio      Cleveland   
 4           335         Prague           wv__Central_Bohemia         Prague   
 ..          ...            ...                           ...            ...   
 401         255       Erlangen                   wv__Bavaria       Erlangen   
 402          99    Guadalajara  wv__Pacific_Coast_28Mexico29    Guadalajara   
 403         253      Eindhoven      wv__Southern_Netherlands      Eindhoven   
 404         232        Chester        wv__North_West_England        Chester   
 405         142           Seeb             wv__Northern_Oman           Seeb   
 
          Country_ID  Type  

In [163]:
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
pd.set_option('display.max_colwidth', -1)

C:\Users\gopin\Anaconda3\lib\site-packages\ipykernel_launcher.py:3: FutureWarning: Passing a negative integer is deprecated in version 1.0 and will not be supported in future version. Instead, use None to not limit the column width.
  This is separate from the ipykernel package so we can avoid doing imports until


In [190]:
print(Location_Data_df['Snippet'][Location_Data_df['Name']=='London'].tolist())

["Europe's financial metropolis and the former heart of the British Empire, packed with all sorts of attractions from sports to museums and two millennia of history."]


In [191]:
Similarity_Dict['London'].iloc[:,[2,3,5,31]]

Name            Country_ID  \
22   Budapest                  Hungary                
279  New York City             United_States          
382  Hong Kong                 China                  
160  Cleveland                 United_States          
306  Prague                    Czech_Republic         
218  Indonesia                 Indonesia              
103  United Kingdom            United_Kingdom         
31   Auckland                  New_Zealand            
77   Amstelveen                Netherlands            
4    Berlin                    Germany                
400  Kansas City               United_States          
8    Melbourne                 Australia              
315  Richmond                  United_States          
67   China                     China                  
319  Rome                      Italy                  
80   Brighton                  United_Kingdom         
191  France                    France                 
261  Mexico                    Mexico                 
268  Monaco                    Monaco                 
396  Essex                     United_States          
3    Paris                     France                 
280  Newark                    United_States          
238  Kyoto                     Japan                  
11   Mississauga               Canada                 
289  Orlando                   United_States          
378  Weybridge                 United_Kingdom         
157  Tokyo/Chiyoda             Japan                  
28   Istanbul                  Turkey                 
346  Taguig                    Philippines            
39   Philadelphia              United_States          
84   Winnipeg                  Canada                 
374  Watford                   United_Kingdom         
101  San Francisco             United_States          
217  Indianapolis              United_States          
223  Irving                    United_States          
159  Brussels                  Belgium                
1    Singapore                 Singapore              
6    Toronto                   Canada                 
16   Atlanta                   United_States          
41   Ottawa                    Canada                 
143  Bournemouth               United_Kingdom         
363  Vienna                    Austria                
9    Tokyo                     Japan                  
108  Cape Town                 South_Africa           
330  Saskatoon                 Canada                 
14   Chicago                   United_States          
79   Edmonton                  Canada                 
399  Republic of Ireland       Republic_of_Ireland    
372  Washington, D.C.          United_States          
297  Philippines               Philippines            
133  Bentonville               United_States          
93   Heilbronn                 Germany                
150  Canberra                  Australia              
344  Surrey                    Canada                 
383  Shanghai                  China                  
152  Cardiff                   United_Kingdom         
125  Baltimore                 United_States          
401  Macau                     China                  
120  Arlington                 United_States          
376  Wellington                New_Zealand            
177  Dresden                   Germany                
59   Jakarta                   Indonesia              
36   Manchester                United_Kingdom         
183  Elizabeth                 United_States          
269  Montreux                  Switzerland            
290  Osh                       Kyrgyzstan             
180  Eastleigh                 United_Kingdom         
233  Khimki                    Russia                 
347  Taipei                    Taiwan                 
389  Zurich                    Switzerland            
45   Sharjah                   United_Arab_Emirates   
373  Waterloo                  Canada                 
270  Mosco

In [192]:
print(Location_Data_df['Snippet'][Location_Data_df['Name']=='Dubai'].tolist())

['Known for coffee. Recommended places to visit are Dubai Museum, Burj Khalifa and Wild Wadi Water Park.']


In [193]:
Similarity_Dict['Dubai'].iloc[:,[2,3,5,31]]

Name            Country_ID  \
102  Abu Dhabi                 United_Arab_Emirates   
255  Manama                    Bahrain                
114  Ajman                     United_Arab_Emirates   
15   Doha                      Qatar                  
179  Durban                    South_Africa           
103  United Kingdom            United_Kingdom         
403  Malé                      Maldives               
345  Swindon                   United_Kingdom         
258  Mecca                     Saudi_Arabia           
80   Brighton                  United_Kingdom         
72   Oxford                    United_Kingdom         
370  Warsaw                    Poland                 
243  Leuven                    Belgium                
24   Riyadh                    Saudi_Arabia           
262  Midrand                   South_Africa           
122  Austin                    United_States          
126  Bangalore                 India                  
228  Kampala                   Uganda                 
74   Kuwait                    Kuwait                 
45   Sharjah                   United_Arab_Emirates   
94   Jeddah                    Saudi_Arabia           
170  Delft                     Netherlands            
43   Mumbai                    India                  
187  Feltham                   United_Kingdom         
23   Houston                   United_States          
360  Venice                    Italy                  
115  Alexandria                Egypt                  
129  Batumi                    Georgia_28country29    
150  Canberra                  Australia              
233  Khimki                    Russia                 
217  Indianapolis              United_States          
40   Miami                     United_States          
26   Stockholm                 Sweden                 
131  Belfast                   United_Kingdom         
1    Singapore                 Singapore              
84   Winnipeg                  Canada                 
78   Muscat                    Oman                   
207  Hanoi                     Vietnam                
373  Waterloo                  Canada                 
311  Reading                   United_Kingdom         
29   Birmingham                United_Kingdom         
232  Kharkiv                   Ukraine                
213  Hiroshima                 Japan                  
22   Budapest                  Hungary                
385  Yerevan                   Armenia                
279  New York City             United_States          
58   Nottingham                United_Kingdom         
193  Fremont                   United_States          
166  Dammam                    Saudi_Arabia           
295  Petaling Jaya             Malaysia               
392  Beijing                   China                  
283  Nijmegen                  Netherlands            
400  Kansas City               United_States          
304  Portland                  United_States          
214  Hyderabad                 India                  
303  Port Louis                Mauritius              
387  Zagreb                    Croatia                
248  Liverpool                 United_Kingdom         
30   Edinburgh                 United_Kingdom         
3    Paris                     France                 
383  Shanghai                  China                  
144  Bratislava                Slovakia               
402  Madison                   United_States          
105  Las Vegas                 United_States          
389  Zurich                    Switzerland            
374  Watford                   United_Kingdom         
378  Weybridge                 United_Kingdom         
87   Hoofddorp                 Netherlands            
9    Tokyo                     Japan                  
35   Dallas                    United_States          
37   Burnaby                   Canada                 
261  Mexico                    Mexico                 
354  Terno

In [194]:
print(Location_Data_df['Snippet'][Location_Data_df['Name']=='Singapore'].tolist())

['Prosperous, clean and orderly island city-state, with a Chinese majority but with strong Malay and Indian communities, the main business and financial hub of the region.']


In [195]:
Similarity_Dict['Singapore'].iloc[:,[2,3,5,31]]

Name            Country_ID  \
180  Eastleigh                 United_Kingdom         
306  Prague                    Czech_Republic         
308  Queenstown                New_Zealand            
106  Kuala Lumpur              Malaysia               
84   Winnipeg                  Canada                 
103  United Kingdom            United_Kingdom         
191  France                    France                 
279  New York City             United_States          
160  Cleveland                 United_States          
405  Virginia                  United_States          
104  Los Angeles               United_States          
218  Indonesia                 Indonesia              
316  Riga                      Latvia                 
67   China                     China                  
157  Tokyo/Chiyoda             Japan                  
162  Columbus                  United_States          
187  Feltham                   United_Kingdom         
27   Vancouver                 Canada                 
7    Sydney                    Australia              
382  Hong Kong                 China                  
123  Australia                 Australia              
270  Moscow                    Russia                 
8    Melbourne                 Australia              
217  Indianapolis              United_States          
372  Washington, D.C.          United_States          
28   Istanbul                  Turkey                 
345  Swindon                   United_Kingdom         
159  Brussels                  Belgium                
297  Philippines               Philippines            
116  Alpharetta                United_States          
383  Shanghai                  China                  
4    Berlin                    Germany                
17   Brampton                  Canada                 
170  Delft                     Netherlands            
185  Espoo                     Finland                
294  Perth                     Australia              
158  Cincinnati                United_States          
401  Macau                     China                  
319  Rome                      Italy                  
262  Midrand                   South_Africa           
144  Bratislava                Slovakia               
107  San Diego                 United_States          
163  Copenhagen                Denmark                
245  Lima                      Peru                   
76   Vantaa                    Finland                
66   Oslo                      Norway                 
37   Burnaby                   Canada                 
36   Manchester                United_Kingdom         
31   Auckland                  New_Zealand            
42   Johannesburg              South_Africa           
222  Irvine                    United_States          
273  Nagoya                    Japan                  
131  Belfast                   United_Kingdom         
188  Ferno                     Italy                  
47   Helsinki                  Finland                
148  Cairns                    Australia              
274  Nanaimo                   Canada                 
101  San Francisco             United_States          
192  Copenhagen/Frederiksberg  Denmark                
314  Richardson                United_States          
397  Hanover                   Germany                
39   Philadelphia              United_States          
9    Tokyo                     Japan                  
91   Adelaide                  Australia              
22   Budapest                  Hungary                
6    Toronto                   Canada                 
298  Phoenix                   United_States          
14   Chicago                   United_States          
0    London                    United_Kingdom         
93   Heilbronn                 Germany                
20   Barcelona                 Spain                  
65   Eschborn                  Germany                
299  Phuke

In [196]:
print(Location_Data_df['Snippet'][Location_Data_df['Name']=='Amsterdam'].tolist())

['Canals, Rembrandt, hashish and red lanterns, the epitome of social liberal attitudes.']


In [197]:
Similarity_Dict['Amsterdam']

Location_ID                              Parent_ID  \
401  wv__Macau                     China                                   
160  Cleveland                     Ohio                                    
27   Vancouver                     wv__British_Columbia                    
157  Chiyoda2C_Tokyo               wv__Kanto                               
347  Taipei                        wv__Northern_Taiwan                     
270  Moscow                        wv__Central_Russia                      
278  New_Delhi                     wv__Plains_28India29                    
22   Budapest                      wv__Central_Hungary                     
67   China                         NaN                                     
8    Melbourne                     wv__Victoria_28state29                  
218  Indonesia                     NaN                                     
3    Paris                         wv__C38Ele-de-France                    
303  Port_Louis                    Mauritius                               
11   Mississauga                   wv__Ontario                             
203  Guelph                        wv__Ontario                             
297  Philippines                   NaN                                     
100  Colombo                       Sri_Lanka                               
6    Toronto                       wv__Ontario                             
23   Houston                       Texas                                   
142  Borehamwood                   wv__East_of_England                     
258  Mecca                         wv__Hejaz                               
363  Vienna                        wv__Lower_Austria                       
318  Roissy-en-France              wv__C38Ele-de-France                    
144  Bratislava                    wv__Western_Slovakia                    
2    Singapore                     NaN                                     
273  Nagoya                        wv__Chubu                               
343  Sunnyvale2C_California        California                              
265  Milwaukee                     Wisconsin                               
31   Auckland                      wv__North_Island                        
42   Johannesburg                  wv__Gauteng                             
279  New_York_City                 New_York_28state29                      
103  United_Kingdom                NaN                                     
216  Incheon                       wv__Gyeonggi                            
46   Interlaken                    wv__Bernese_Highlands                   
105  Las_Vegas                     Nevada                                  
372  Washington2C_D2eC2e           United_States                           
101  San_Francisco                 California                              
269  Montreux                      wv__Western_Switzerland                 
116  Alpharetta2C_Georgia          Georgia_28U2eS2e_state29                
80   Brighton                      wv__South_East_England                  
340  Stockport                     wv__North_West_England                  
39   Philadelphia                  Pennsylvania                            
290  Osh                           wv__Ferghana_Valley_28Kyrgyzstan29      
300  Pisa                          wv__Tuscany                             
325  San_Jose2C_California         California                              
72   Oxford                        wv__South_East_England                  
183  Elizabeth2C_New_Jersey        New_Jersey                              
373  Waterloo2C_Ontario            wv__Ontario                             
21   Luxembourg                    NaN                                     
387  Zagreb                        wv__Central_Croatia                     
212  Hilversum                     wv__Western_Netherlands                 
306  Prague                        wv__Central_Bohemia                

In [198]:
print(Location_Data_df['Snippet'][Location_Data_df['Name']=='Paris'].tolist())

['The "City of Light" and one of the most visited places on Earth: romance, cuisine, the Eiffel Tower and a surprising amount of green await you.']


In [199]:
Similarity_Dict['Paris']

Location_ID                              Parent_ID  \
363  Vienna                        wv__Lower_Austria                       
306  Prague                        wv__Central_Bohemia                     
20   Barcelona                     wv__Catalonia                           
258  Mecca                         wv__Hejaz                               
278  New_Delhi                     wv__Plains_28India29                    
23   Houston                       Texas                                   
207  Hanoi                         wv__Northern_Vietnam                    
303  Port_Louis                    Mauritius                               
319  Rome                          wv__Lazio                               
281  Niagara_Falls2C_Ontario       wv__Ontario                             
103  United_Kingdom                NaN                                     
279  New_York_City                 New_York_28state29                      
21   Luxembourg                    NaN                                     
22   Budapest                      wv__Central_Hungary                     
101  San_Francisco                 California                              
392  wv__Beijing                   China                                   
214  Hyderabad                     wv__Southern_India                      
262  Midrand                       wv__Gauteng                             
3    Amsterdam                     wv__Western_Netherlands                 
77   Amstelveen                    wv__Western_Netherlands                 
76   Vantaa                        wv__Southern_Finland                    
374  Watford                       wv__East_of_England                     
5    Seattle                       Washington_28state29                    
100  Colombo                       Sri_Lanka                               
87   Hoofddorp                     wv__Western_Netherlands                 
2    Singapore                     NaN                                     
31   Auckland                      wv__North_Island                        
289  Orlando2C_Florida             Florida                                 
393  Berkeley2C_California         California                              
247  Lisbon                        wv__Lisbon_Region                       
54   Calgary                       wv__Prairies                            
370  Warsaw                        wv__Mazowieckie                         
210  Helsingborg                   wv__GC3B6taland                         
295  Petaling_Jaya                 wv__West_Coast_28Malaysia29             
300  Pisa                          wv__Tuscany                             
302  Plymouth                      wv__West_Country                        
160  Cleveland                     Ohio                                    
24   Riyadh                        wv__Nejd                                
39   Philadelphia                  Pennsylvania                            
234  Khobar                        wv__Eastern_Province_28Saudi_Arabia29   
383  wv__Shanghai                  China                                   
287  Oklahoma_City                 Oklahoma                                
4    Berlin                        wv__Brandenburg                         
99   Christchurch                  wv__South_Island                        
261  Mexico                        NaN                                     
183  Elizabeth2C_New_Jersey        New_Jersey                              
297  Philippines                   NaN                                     
218  Indonesia                     NaN                                     
317  Rochester2C_New_York          New_York_28state29                      
144  Bratislava                    wv__Western_Slovakia                    
142  Borehamwood                   wv__East_of_England                     
154  Charlotte2C_North_Carolina    North_Carolina                     

In [200]:
print(Location_Data_df['Snippet'][Location_Data_df['Name']=='Berlin'].tolist())

["Scarred by four decades of division but experiencing an almost unprecedented boom, the capital of reunited Germany is one of Europe's most creative and innovative cities and still surprisingly affordable."]


In [201]:
Similarity_Dict['Berlin']

Location_ID                              Parent_ID  \
21   Luxembourg                    NaN                                     
306  Prague                        wv__Central_Bohemia                     
77   Amstelveen                    wv__Western_Netherlands                 
270  Moscow                        wv__Central_Russia                      
99   Christchurch                  wv__South_Island                        
160  Cleveland                     Ohio                                    
20   Barcelona                     wv__Catalonia                           
187  Feltham                       wv__South_East_England                  
345  Swindon                       wv__West_Country                        
67   China                         NaN                                     
4    Paris                         wv__C38Ele-de-France                    
363  Vienna                        wv__Lower_Austria                       
31   Auckland                      wv__North_Island                        
103  United_Kingdom                NaN                                     
268  Monaco                        NaN                                     
319  Rome                          wv__Lazio                               
180  Eastleigh                     wv__South_East_England                  
101  San_Francisco                 California                              
383  wv__Shanghai                  China                                   
279  New_York_City                 New_York_28state29                      
22   Budapest                      wv__Central_Hungary                     
191  France                        NaN                                     
0    London                        United_Kingdom                          
87   Hoofddorp                     wv__Western_Netherlands                 
185  Espoo                         wv__Southern_Finland                    
297  Philippines                   NaN                                     
168  Davao_City                    wv__Mindanao                            
372  Washington2C_D2eC2e           United_States                           
159  City_of_Brussels              wv__Flanders                            
374  Watford                       wv__East_of_England                     
14   Chicago                       Illinois                                
218  Indonesia                     NaN                                     
254  MalmC3B6                      wv__GC3B6taland                         
328  Santiago                      wv__Central_Chile                       
106  Kuala_Lumpur                  wv__West_Coast_28Malaysia29             
2    Singapore                     NaN                                     
396  Essex2C_Connecticut           Connecticut                             
74   Kuwait                        NaN                                     
144  Bratislava                    wv__Western_Slovakia                    
391  Atlantic_City2C_New_Jersey    New_Jersey                              
8    Melbourne                     wv__Victoria_28state29                  
192  Frederiksberg                 wv__Zealand                             
28   Istanbul                      wv__Marmara_28region29                  
148  Cairns                        wv__Queensland                          
274  Nanaimo                       wv__British_Columbia                    
222  Irvine2C_California           California                              
37   Burnaby                       wv__British_Columbia                    
27   Vancouver                     wv__British_Columbia                    
261  Mexico                        NaN                                     
11   Mississauga                   wv__Ontario                             
378  Weybridge                     wv__South_East_England                  
123  Australia                     NaN                                

In [174]:
print(Location_Data_df['Snippet'][Location_Data_df['Name']=='Seattle'].tolist())

['Known for natural attractions. Recommended places to visit are Seattle Art Museum, Space Needle and Museum of Flight.']


In [202]:
Similarity_Dict['Seattle']

Location_ID                              Parent_ID  \
241  Leicester                     wv__East_Midlands                       
292  Pasay                         wv__Luzon                               
353  Tempe2C_Arizona               Arizona                                 
289  Orlando2C_Florida             Florida                                 
55   Coventry                      wv__West_Midlands_28region29            
24   Riyadh                        wv__Nejd                                
324  San_Antonio                   Texas                                   
304  Portland2C_Oregon             Oregon                                  
35   Dallas                        Texas                                   
265  Milwaukee                     Wisconsin                               
40   Miami                         Florida                                 
122  Austin2C_Texas                Texas                                   
385  Yerevan                       wv__Central_Armenia                     
173  Detroit                       Michigan                                
245  Lima                          wv__Central_Coast_28Peru29              
154  Charlotte2C_North_Carolina    North_Carolina                          
23   Houston                       Texas                                   
314  Richardson2C_Texas            Texas                                   
85   Denver                        Colorado                                
101  San_Francisco                 California                              
222  Irvine2C_California           California                              
280  Newark2C_New_Jersey           New_Jersey                              
286  Nuneaton                      wv__West_Midlands_28region29            
266  Minneapolis                   Minnesota                               
149  Cairo                         wv__Lower_Egypt                         
158  Cincinnati                    Ohio                                    
270  Moscow                        wv__Central_Russia                      
193  Fremont2C_California          California                              
37   Burnaby                       wv__British_Columbia                    
207  Hanoi                         wv__Northern_Vietnam                    
33   Montreal                      wv__Quebec                              
298  Phoenix2C_Arizona             Arizona                                 
274  Nanaimo                       wv__British_Columbia                    
217  Indianapolis                  Indiana                                 
357  Tver                          wv__Central_Russia                      
348  Tampa2C_Florida               Florida                                 
97   Makati                        wv__Luzon                               
64   Brisbane                      wv__Queensland                          
394  Brisbane                      wv__Queensland                          
93   Heilbronn                     wv__Baden-WC3BCrttemberg                
68   Nairobi                       wv__Southern_Rift_Valley                
214  Hyderabad                     wv__Southern_India                      
303  Port_Louis                    Mauritius                               
4    Paris                         wv__C38Ele-de-France                    
138  Bloomington2C_Indiana         Indiana                                 
290  Osh                           wv__Ferghana_Valley_28Kyrgyzstan29      
223  Irving2C_Texas                Texas                                   
79   Edmonton                      wv__Prairies                            
160  Cleveland                     Ohio                                    
387  Zagreb                        wv__Central_Croatia                     
125  Baltimore                     Maryland                                
135  Bern                          wv__Bernese_Highlands              

In [178]:
print(Location_Data_df['Snippet'][Location_Data_df['Name']=='Toronto'].tolist())

["Canada's largest city, a cosmopolitan mosaic with ethnic enclaves and cultural attractions galore."]


In [203]:
Similarity_Dict['Toronto']

Location_ID                              Parent_ID  \
218  Indonesia                     NaN                                     
372  Washington2C_D2eC2e           United_States                           
279  New_York_City                 New_York_28state29                      
27   Vancouver                     wv__British_Columbia                    
180  Eastleigh                     wv__South_East_England                  
383  wv__Shanghai                  China                                   
41   Ottawa                        wv__Ontario                             
297  Philippines                   NaN                                     
373  Waterloo2C_Ontario            wv__Ontario                             
7    Sydney                        wv__New_South_Wales                     
187  Feltham                       wv__South_East_England                  
160  Cleveland                     Ohio                                    
67   China                         NaN                                     
8    Melbourne                     wv__Victoria_28state29                  
345  Swindon                       wv__West_Country                        
2    Singapore                     NaN                                     
363  Vienna                        wv__Lower_Austria                       
191  France                        NaN                                     
14   Chicago                       Illinois                                
9    Tokyo                         wv__Kanto                               
0    London                        United_Kingdom                          
28   Istanbul                      wv__Marmara_28region29                  
330  Saskatoon                     wv__Prairies                            
344  Surrey2C_British_Columbia     wv__British_Columbia                    
216  Incheon                       wv__Gyeonggi                            
306  Prague                        wv__Central_Bohemia                     
22   Budapest                      wv__Central_Hungary                     
106  Kuala_Lumpur                  wv__West_Coast_28Malaysia29             
96   Vaughan                       wv__Ontario                             
59   Jakarta                       wv__Java                                
290  Osh                           wv__Ferghana_Valley_28Kyrgyzstan29      
51   Puteaux                       wv__C38Ele-de-France                    
123  Australia                     NaN                                     
37   Burnaby                       wv__British_Columbia                    
376  Wellington                    wv__North_Island                        
274  Nanaimo                       wv__British_Columbia                    
291  Oshawa                        wv__Ontario                             
159  City_of_Brussels              wv__Flanders                            
103  United_Kingdom                NaN                                     
101  San_Francisco                 California                              
31   Auckland                      wv__North_Island                        
144  Bratislava                    wv__Western_Slovakia                    
255  Manama                        Bahrain                                 
174  Dhaka                         wv__Dhaka_Division                      
36   Manchester                    wv__North_West_England                  
39   Philadelphia                  Pennsylvania                            
318  Roissy-en-France              wv__C38Ele-de-France                    
316  Riga                          wv__Riga_region                         
79   Edmonton                      wv__Prairies                            
152  Cardiff                       wv__South_Wales                         
91   Adelaide                      wv__South_Australia                     
15   Doha                          Qatar                              

In [180]:
print(Location_Data_df['Snippet'][Location_Data_df['Name']=='Sydney'].tolist())

['The capital of the state and largest city in Australia, and its suburban surroundings, forms its own vibrant region.']


In [204]:
Similarity_Dict['Sydney']

Location_ID                              Parent_ID  \
372  Washington2C_D2eC2e           United_States                           
47   Helsinki                      wv__Southern_Finland                    
28   Istanbul                      wv__Marmara_28region29                  
262  Midrand                       wv__Gauteng                             
144  Bratislava                    wv__Western_Slovakia                    
160  Cleveland                     Ohio                                    
27   Vancouver                     wv__British_Columbia                    
316  Riga                          wv__Riga_region                         
5    Berlin                        wv__Brandenburg                         
162  Columbus2C_Ohio               Ohio                                    
84   Winnipeg                      wv__Prairies                            
99   Christchurch                  wv__South_Island                        
17   Brampton                      wv__Ontario                             
170  Delft                         wv__Western_Netherlands                 
20   Barcelona                     wv__Catalonia                           
180  Eastleigh                     wv__South_East_England                  
103  United_Kingdom                NaN                                     
297  Philippines                   NaN                                     
217  Indianapolis                  Indiana                                 
14   Chicago                       Illinois                                
191  France                        NaN                                     
294  Perth                         wv__Western_Australia                   
158  Cincinnati                    Ohio                                    
106  Kuala_Lumpur                  wv__West_Coast_28Malaysia29             
107  San_Diego                     California                              
131  Belfast                       wv__Northern_Ireland                    
194  Galway                        wv__West_Ireland                        
405  Virginia                      United_States                           
306  Prague                        wv__Central_Bohemia                     
7    Toronto                       wv__Ontario                             
2    Singapore                     NaN                                     
37   Burnaby                       wv__British_Columbia                    
159  City_of_Brussels              wv__Flanders                            
308  Queenstown2C_New_Zealand      wv__South_Island                        
270  Moscow                        wv__Central_Russia                      
77   Amstelveen                    wv__Western_Netherlands                 
187  Feltham                       wv__South_East_England                  
110  Aachen                        wv__North_Rhine-Westphalia              
379  Windsor2C_Ontario             wv__Ontario                             
67   China                         NaN                                     
373  Waterloo2C_Ontario            wv__Ontario                             
101  San_Francisco                 California                              
399  Republic_of_Ireland           NaN                                     
123  Australia                     NaN                                     
148  Cairns                        wv__Queensland                          
345  Swindon                       wv__West_Country                        
93   Heilbronn                     wv__Baden-WC3BCrttemberg                
288  Orenburg                      wv__Urals                               
39   Philadelphia                  Pennsylvania                            
298  Phoenix2C_Arizona             Arizona                                 
185  Espoo                         wv__Southern_Finland                    
91   Adelaide                      wv__South_Australia                

In [183]:
print(Location_Data_df['Snippet'][Location_Data_df['Name']=='Melbourne'].tolist())

['Multicultural and sports-mad, this vibrant city includes many cultural institutions.']


In [205]:
Similarity_Dict['Melbourne']

Location_ID                              Parent_ID  \
306  Prague                        wv__Central_Bohemia                     
27   Vancouver                     wv__British_Columbia                    
279  New_York_City                 New_York_28state29                      
7    Toronto                       wv__Ontario                             
31   Auckland                      wv__North_Island                        
372  Washington2C_D2eC2e           United_States                           
160  Cleveland                     Ohio                                    
103  United_Kingdom                NaN                                     
144  Bratislava                    wv__Western_Slovakia                    
318  Roissy-en-France              wv__C38Ele-de-France                    
297  Philippines                   NaN                                     
0    London                        United_Kingdom                          
22   Budapest                      wv__Central_Hungary                     
2    Singapore                     NaN                                     
67   China                         NaN                                     
319  Rome                          wv__Lazio                               
157  Chiyoda2C_Tokyo               wv__Kanto                               
363  Vienna                        wv__Lower_Austria                       
185  Espoo                         wv__Southern_Finland                    
104  Los_Angeles                   California                              
218  Indonesia                     NaN                                     
280  Newark2C_New_Jersey           New_Jersey                              
216  Incheon                       wv__Gyeonggi                            
328  Santiago                      wv__Central_Chile                       
399  Republic_of_Ireland           NaN                                     
383  wv__Shanghai                  China                                   
8    Sydney                        wv__New_South_Wales                     
116  Alpharetta2C_Georgia          Georgia_28U2eS2e_state29                
21   Luxembourg                    NaN                                     
376  Wellington                    wv__North_Island                        
353  Tempe2C_Arizona               Arizona                                 
385  Yerevan                       wv__Central_Armenia                     
397  Hanover                       wv__Lower_Saxony                        
3    Amsterdam                     wv__Western_Netherlands                 
270  Moscow                        wv__Central_Russia                      
5    Berlin                        wv__Brandenburg                         
87   Hoofddorp                     wv__Western_Netherlands                 
74   Kuwait                        NaN                                     
314  Richardson2C_Texas            Texas                                   
244  Lille                         wv__Hauts-de-France                     
289  Orlando2C_Florida             Florida                                 
77   Amstelveen                    wv__Western_Netherlands                 
122  Austin2C_Texas                Texas                                   
401  wv__Macau                     China                                   
223  Irving2C_Texas                Texas                                   
42   Johannesburg                  wv__Gauteng                             
359  Valencia                      wv__Valencian_Community                 
36   Manchester                    wv__North_West_England                  
99   Christchurch                  wv__South_Island                        
101  San_Francisco                 California                              
222  Irvine2C_California           California                              
290  Osh                           wv__Ferghana_Valley_28Kyrgyzstan29 